In [ ]:
%matplotlib inline


# Create a surrogate discipline

We want to build an :class:`.MDODiscipline`
based on a regression model approximating the following discipline
with two inputs and two outputs:

- $y_1=1+2x_1+3x_2$
- $y_2=-1-2x_1-3x_2$

over the unit hypercube $[0,1]\times[0,1]$.
For that, we use a :class:`.SurrogateDiscipline` relying on a :class:`.MLRegressionAlgo`


In [ ]:
from __future__ import annotations

from gemseo.api import configure_logger
from gemseo.api import create_design_space
from gemseo.api import create_discipline
from gemseo.api import create_scenario
from gemseo.api import create_surrogate
from numpy import array

## Import



In [ ]:
configure_logger()

## Create the discipline to learn
We can implement this analytic discipline by means of the
:class:`~gemseo.disciplines.analytic.AnalyticDiscipline` class.



In [ ]:
expressions = {"y_1": "1+2*x_1+3*x_2", "y_2": "-1-2*x_1-3*x_2"}
discipline = create_discipline(
    "AnalyticDiscipline", name="func", expressions=expressions
)

## Create the input sampling space
We create the input sampling space by adding the variables one by one.



In [ ]:
design_space = create_design_space()
design_space.add_variable("x_1", l_b=0.0, u_b=1.0)
design_space.add_variable("x_2", l_b=0.0, u_b=1.0)

## Create the learning set
We can build a learning set by means of a
:class:`~gemseo.core.doe_scenario.DOEScenario` with a full factorial design of
experiments. The number of samples can be equal to 9 for example.



In [ ]:
scenario = create_scenario(
    [discipline], "DisciplinaryOpt", "y_1", design_space, scenario_type="DOE"
)
scenario.execute({"algo": "fullfact", "n_samples": 9})

## Create the surrogate discipline
Then, we build the Gaussian process regression model from the database and
displays this model.



In [ ]:
dataset = scenario.export_to_dataset(opt_naming=False)
model = create_surrogate("GaussianProcessRegressor", data=dataset)

## Predict output
Once it is built, we can use it for prediction, either with default inputs
or with user-defined ones.



In [ ]:
print(model.execute())
input_value = {"x_1": array([1.0]), "x_2": array([2.0])}
output_value = model.execute(input_value)
print(output_value)